In [0]:
%pip install openpyxl
%pip install pytest

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


1. Read the provided files into dataframes

In [0]:
import pandas as pd
import json
from datetime import datetime

# Load Orders JSON file
with open('/Volumes/workspace/default/temp/Orders.json', 'r') as f:
    orders_data = json.load(f)
orders_df = pd.DataFrame(orders_data)

# Load Products CSV
products_df = pd.read_csv('/Volumes/workspace/default/temp/Products.csv')

# Load Customer Excel file  
customers_df = pd.read_excel('/Volumes/workspace/default/temp/Customer.xlsx')


In [0]:
customers_df= customers_df.drop('phone', axis=1)  # dropping column with bad data (unneccasry, as not being used anywhere)

2. Data Cleaning and Date Processing

In [0]:
# Parse date function
def parse_date(date_str):
    try:
        return pd.to_datetime(date_str, format='%d/%m/%Y')
    except:
        return pd.NaT

# Transform dates and extract year
orders_df['Order Date'] = orders_df['Order Date'].apply(parse_date)
orders_df['Ship Date'] = orders_df['Ship Date'].apply(parse_date)
orders_df['Year'] = orders_df['Order Date'].dt.year


In [0]:

%sql
Drop Table orders;
Drop Table products;
Drop Table customers;



In [0]:
from pyspark.sql.functions import trim, regexp_replace, when, col


# save raw tables
#Rename Columns to remove spaces

orders_df = orders_df.rename(columns=lambda x: x.replace(" ", "_"))
products_df = products_df.rename(columns=lambda x: x.replace(" ", "_"))
customers_df = customers_df.rename(columns=lambda x: x.replace(" ", "_"))

spark_orders_df = spark.createDataFrame(orders_df)
spark_products_df = spark.createDataFrame(products_df)
spark_customers_df = spark.createDataFrame(customers_df)

spark_orders_df = spark_orders_df.dropna()
spark_customers_df = spark_customers_df.dropna()

spark_customers_df = spark_customers_df.withColumn(
    "Customer_Name",
    trim(
        regexp_replace(
            regexp_replace("Customer_Name", "[^a-zA-Z ]", ""),  # remove special chars and digits from customer name
            " +",  # regex for one or more spaces
            " "    # replace with single space
        )
    )
)



spark_orders_df.write.mode("overwrite").saveAsTable("orders")
spark_products_df.write.mode("overwrite").saveAsTable("products")
spark_customers_df.write.mode("overwrite").saveAsTable("customers")

3. Unit Tests For Data Cleaning
Test the Data Cleaning logic, including column renaming and handling missing values

In [0]:
import pytest

def test_column_renaming():
    # Test that column renaming works correctly for already built DataFrames
    assert "Order_ID" in spark_orders_df.columns, "Column renaming failed for Orders DataFrame."
    assert "Product_ID" in spark_products_df.columns, "Column renaming failed for Products DataFrame."
    assert "Customer_ID" in spark_customers_df.columns, "Column renaming failed for Customers DataFrame."

def test_dropna_orders():
    # Test that rows with missing values are dropped in orders DataFrame
    total_rows = spark.createDataFrame(orders_df).count()
    cleaned_rows = spark_orders_df.count()
    assert cleaned_rows <= total_rows, "Dropna failed to clean missing rows in Orders DataFrame."

def test_dropna_customers():
    # Test that rows with missing values are dropped in customers DataFrame
    total_rows = spark.createDataFrame(customers_df).count()
    cleaned_rows = spark_customers_df.count()
    assert cleaned_rows <= total_rows, "Dropna failed to clean missing rows in Customers DataFrame."

4. Create tables with additional details and Respective unit tests


In [0]:
# Ensure spark_orders_df is defined by reading from the saved table if not already present
if 'spark_orders_df' not in locals():
    spark_orders_df = spark.table("orders")
if 'spark_customers_df' not in locals():
    spark_customers_df = spark.table("customers")

from pyspark.sql import functions as F

# Aggregate customer metrics - To get order information
customer_metrics = spark_orders_df.groupby('Customer_ID').agg(
    F.countDistinct('Order_ID').alias('Total_Orders'),
    F.sum('Price').alias('Total_Sales'),
    F.sum('Profit').alias('Total_Profit'),
    F.sum('Quantity').alias('Total_Quantity'),
    F.min('Order_Date').alias('First_Order_Date'),
    F.max('Order_Date').alias('Last_Order_Date')
)

# Round the numeric columns
customer_metrics = customer_metrics.withColumn('Total_Sales', F.round('Total_Sales', 2)) \
                                   .withColumn('Total_Profit', F.round('Total_Profit', 2)) \
                                   .withColumn('Total_Quantity', F.round('Total_Quantity', 2))

# Join with customer details, Left join with Customer and Customer Metrics  
enriched_customers = spark_customers_df.join(
    customer_metrics,
    on='Customer_ID',
    how='left'
)

display(enriched_customers)

# Additional unit tests
def test_customer_metrics_columns():
    expected_columns = {
        'Customer_ID', 'Total_Orders', 'Total_Sales', 'Total_Profit',
        'Total_Quantity', 'First_Order_Date', 'Last_Order_Date'
    }
    actual_columns = set(customer_metrics.columns)
    assert expected_columns.issubset(actual_columns), "Customer metrics columns missing."

def test_enriched_customers_join():
    # All Customer_IDs in spark_customers_df should be present in enriched_customers
    customer_ids = set(row['Customer_ID'] for row in spark_customers_df.select('Customer_ID').collect())
    enriched_ids = set(row['Customer_ID'] for row in enriched_customers.select('Customer_ID').collect())
    assert customer_ids.issubset(enriched_ids), "Left join failed: missing Customer_IDs in enriched_customers."

def test_total_orders_non_negative():
    # Total_Orders should be non-negative
    min_orders = customer_metrics.agg(F.min('Total_Orders')).collect()[0][0]
    assert min_orders >= 0, "Total_Orders contains negative values."

def test_total_sales_profit_quantity_non_negative():
    # Total_Sales, Total_Profit, and Total_Quantity should be non-negative or null
    for col_name in ['Total_Sales', 'Total_Profit', 'Total_Quantity']:
        min_value = customer_metrics.agg(F.min(col_name)).collect()[0][0]
        assert (min_value is None) or (min_value >= 0), f"{col_name} contains negative values."

def test_first_last_order_date_order():
    # First_Order_Date should be less than or equal to Last_Order_Date
    rows = customer_metrics.select('First_Order_Date', 'Last_Order_Date').collect()
    for row in rows:
        if row['First_Order_Date'] and row['Last_Order_Date']:
            assert row['First_Order_Date'] <= row['Last_Order_Date'], "First_Order_Date is after Last_Order_Date."

Customer_ID Customer_Name email address Segment Country City State Postal_Code Region Total_Orders Total_Sales Total_Profit Total_Quantity First_Order_Date Last_Order_Date RD-19585 Rob Dowd danielleware947@gmail.com 1055 Leslie Squares Apt. 640
North Jacob, AZ 25423 Consumer United States Dubuque Iowa 52001 Central 10 2912.66 734.52 73 2014-04-02T00:00:00.000Z 2017-07-03T00:00:00.000Z MM-18055 Michelle Moray andrewhays420@gmail.com 1127 Cole Skyway
Lake Steven, OK 62340 Consumer United States San Francisco California 94110 West 8 2749.86 -520.46 73 2014-04-11T00:00:00.000Z 2017-10-30T00:00:00.000Z FO-14305 Frank Olsen kendraholder796@gmail.com 0543 Martinez Mount Suite 497
South Johnfort, NM 85655 Consumer United States Philadelphia Pennsylvania 19143 East 10 2678.43 215.58 60 2014-06-09T00:00:00.000Z 2017-11-22T00:00:00.000Z MP-17470 Mark Packer nicholasrobinson191@gmail.com 143 Kyle Throughway Suite 713
North Jacobville, SC 41104 Home Office United States New York City New York 10035 East 7 3205.77 600.3 77 2014-03-30T00:00:00.000Z 2016-01-11T00:00:00.000Z CM-12115 Chad McGuire sharonwarner980@gmail.com 050 Anna Camp
South Jonathan, WY 45473 Consumer United States New York City New York 10011 East 4 1661.61 408.58 35 2015-03-29T00:00:00.000Z 2017-12-22T00:00:00.000Z KN-16705 Kristina Nunn sabrinahayes269@gmail.com 04950 Joseph Meadow
East Kyleville, FM 82237 Home Office United States Sparks Nevada 89431 West 8 2280.58 329.77 55 2014-03-02T00:00:00.000Z 2017-09-23T00:00:00.000Z JG-15310 Jason Gross danielpaul555@gmail.com 04852 Wise Row
Davidfurt, AR 32041 Corporate United States Newark Ohio 43055 East 6 2240.58 3.59 46 2016-03-03T00:00:00.000Z 2017-12-28T00:00:00.000Z VM-21685 Valerie Mitchum pamelathompson911@gmail.com 0592 James Landing Apt. 950
East Steven, NJ 78538 Home Office United States Seattle Washington 98105 West 7 2454.12 513.62 37 2014-04-07T00:00:00.000Z 2017-11-06T00:00:00.000Z TS-21085 Thais Sissman jamesjohnson660@gmail.com 04890 Sweeney Turnpike
East Mariaside, DC 09754 Consumer United States Ormond Beach Florida 32174 South 2 4.83 -3.32 4 2015-07-19T00:00:00.000Z 2017-01-07T00:00:00.000Z FM-14290 Frank Merwin denisecook866@gmail.com 143 Danielle Route
New Seanburgh, FM 77823 Home Office United States Quincy Massachusetts 2169 East 9 3736.23 197.89 79 2014-08-26T00:00:00.000Z 2017-11-24T00:00:00.000Z JM-15655 Jim Mitchum laurenperez268@gmail.com 122 Garcia Loop Suite 998
Zacharyhaven, VI 36852 Corporate United States Bridgeton New Jersey 8302 East 5 864.95 117.2 41 2014-04-08T00:00:00.000Z 2017-12-22T00:00:00.000Z QJ-19255 Quincy Jones brandonlee327@gmail.com 1603 Robin Stream Suite 668
South Douglas, NM 62416 Corporate United States Burlington Vermont 5408 East 9 6108.34 1203.69 61 2014-03-17T00:00:00.000Z 2017-12-05T00:00:00.000Z CD-12280 Christina DeMoss josephsparks348@gmail.com 10888 Ortiz Circle Suite 427
East Karen, CT 17147 Consumer United States Seattle Washington 98105 West 2 1205.58 233.48 39 2017-11-05T00:00:00.000Z 2017-11-18T00:00:00.000Z DB-13615 Doug Bickford robertbryan207@gmail.com 1631 Moore Streets
Theresaport, WA 23450 Consumer United States Asheville North Carolina 28806 South 7 1989.05 438.8 41 2014-09-30T00:00:00.000Z 2017-11-27T00:00:00.000Z TB-21520 Tracy Blumstein codysalinas340@gmail.com 066 Stephanie Center Suite 944
Lake Brandonfort, WA 29497 Consumer United States Philadelphia Pennsylvania 19140 East 9 4737.48 -1603.04 85 2014-10-17T00:00:00.000Z 2017-09-14T00:00:00.000Z RM-19750 Roland Murray caseyrobbins335@gmail.com 129 Deborah Junctions
Danielleside, FL 80925 Consumer United States New York City New York 10011 East 1 98.35 28.68 4 2017-03-06T00:00:00.000Z 2017-03-06T00:00:00.000Z AS-10135 Adrian Shami patriciajones445@gmail.com 098 Shelly Dale Apt. 244
Delgadoshire, SD 26738 Home Office United States Auburn Washington 98002 West 2 58.54 21.84 9 2016-11-13T00:00:00.000Z 2017-11-19T00:00:00.000Z NP-18670 Nra Paige rodneysutton737@gmail.com 10316 Debra Unions
South Melody, IL

In [0]:
# Ensure spark_products_df is defined by reading from the saved table if not already present
if 'spark_products_df' not in locals():
    spark_products_df = spark.table("products")

product_metrics = spark_orders_df.groupby('Product_ID').agg(
    F.countDistinct('Order_ID').alias('Total_Orders'),
    F.sum('Price').alias('Total_Sales'),
    F.sum('Profit').alias('Total_Profit'),
    F.sum('Quantity').alias('Total_Quantity_Sold'),
    F.countDistinct('Customer_ID').alias('Unique_Customers')
)

product_metrics = product_metrics.withColumn('Total_Sales', F.round('Total_Sales', 2)) \
                                .withColumn('Total_Profit', F.round('Total_Profit', 2))

# Join with product details, Left join 
enriched_products = spark_products_df.join(product_metrics,
                                    on='Product_ID',
                                    how='left')

display(enriched_products)

# Pytest unit tests for product_metrics and enriched_products
def test_product_metrics_columns():
    expected_columns = {
        'Product_ID', 'Total_Orders', 'Total_Sales', 'Total_Profit',
        'Total_Quantity_Sold', 'Unique_Customers'
    }
    actual_columns = set(product_metrics.columns)
    assert expected_columns.issubset(actual_columns), "Product metrics columns missing."

def test_enriched_products_join():
    # All Product_IDs in spark_products_df should be present in enriched_products
    product_ids = set(row['Product_ID'] for row in spark_products_df.select('Product_ID').collect())
    enriched_ids = set(row['Product_ID'] for row in enriched_products.select('Product_ID').collect())
    assert product_ids.issubset(enriched_ids), "Left join failed: missing Product_IDs in enriched_products."

def test_total_orders_non_negative_products():
    # Total_Orders should be non-negative
    min_orders = product_metrics.agg(F.min('Total_Orders')).collect()[0][0]
    assert min_orders >= 0, "Total_Orders contains negative values in product_metrics."

def test_total_sales_profit_non_negative_products():
    # Total_Sales and Total_Profit should be non-negative or null
    for col_name in ['Total_Sales', 'Total_Profit']:
        min_value = product_metrics.agg(F.min(col_name)).collect()[0][0]
        assert (min_value is None) or (min_value >= 0), f"{col_name} contains negative values in product_metrics."

def test_total_quantity_sold_non_negative():
    # Total_Quantity_Sold should be non-negative or null
    min_value = product_metrics.agg(F.min('Total_Quantity_Sold')).collect()[0][0]
    assert (min_value is None) or (min_value >= 0), "Total_Quantity_Sold contains negative values in product_metrics."

def test_unique_customers_non_negative():
    # Unique_Customers should be non-negative
    min_value = product_metrics.agg(F.min('Unique_Customers')).collect()[0][0]
    assert (min_value is None) or (min_value >= 0), "Unique_Customers contains negative values in product_metrics."

Product_ID Category Sub-Category Product_Name State Price_per_product Total_Orders Total_Sales Total_Profit Total_Quantity_Sold Unique_Customers OFF-ST-10001128 Office Supplies Storage Carina Mini System Audio Rack, Model AR050B Indiana 110.75 6 2729.19 -68.8 26 6 OFF-BI-10001249 Office Supplies Binders Avery Heavy-Duty EZD View Binder with Locking Rings Illinois 1.276 10 170.99 29.72 41 10 OFF-PA-10004243 Office Supplies Paper Xerox 1939 New Jersey 18.97 5 417.34 200.33 22 5 OFF-PA-10001800 Office Supplies Paper Xerox 220 California 6.48 8 145.15 60.91 25 8 OFF-PA-10001790 Office Supplies Paper Xerox 1910 Illinois 38.432 5 586.09 236.36 14 5 TEC-PH-10002824 Technology Phones Jabra SPEAK 410 Multidevice Speakerphone Ohio 123.3333333 3 2017.96 10.3 13 3 OFF-AP-10000358 Office Supplies Appliances Fellowes Basic Home/Office Series Surge Protectors Illinois 2.596 9 436.27 58.69 41 9 OFF-BI-10001308 Office Supplies Binders GBC Standard Plastic Binding Systems' Combs Texas 1.256 8 108.65 5.21 30 8 FUR-TA-10004619 Furniture Tables Hon Non-Folding Utility Tables Texas 111.517 5 3775.52 541.66 29 5 OFF-BI-10001097 Office Supplies Binders Avery Hole Reinforcements Washington 4.666666667 9 115.57 15.15 32 9 TEC-PH-10003442 Technology Phones Samsung Replacement EH64AVFWE Premium Headset New York 5.5 5 104.5 17.89 21 5 OFF-PA-10003039 Office Supplies Paper Xerox 1960 California 30.98 6 879.83 334.58 32 6 OFF-AR-10003876 Office Supplies Art Avery Hi-Liter GlideStik Fluorescent Highlighter, Yellow Ink New York 3.26 2 26.08 9.65 9 2 FUR-TA-10003392 Furniture Tables Global Adaptabilities Conference Tables Kentucky 280.98 4 3540.35 354.04 14 4 FUR-FU-10000308 Furniture Furnishings Deflect-o Glass Clear Studded Chair Mats Wisconsin 62.18 7 1579.14 318.37 26 7 FUR-FU-10001706 Furniture Furnishings Longer-Life Soft White Bulbs New York 3.08 10 115.57 44.74 44 10 OFF-ST-10000649 Office Supplies Storage Hanging Personal Folder File Ohio 12.5 5 251.08 51.32 17 5 OFF-PA-10003177 Office Supplies Paper Xerox 1999 Washington 6.0 7 97.53 41.2 17 7 TEC-PH-10002660 Technology Phones Nortel Networks T7316 E Nt8 B27 Michigan 67.99 6 1876.6 397.94 29 6 OFF-BI-10003707 Office Supplies Binders Aluminum Screw Posts Texas 3.052 11 353.72 41.19 41 11 OFF-BI-10001524 Office Supplies Binders GBC Premium Transparent Covers with Diagonal Lined Pattern New York 16.784 14 780.1 49.76 67 14 OFF-PA-10001970 Office Supplies Paper Xerox 1881 Minnesota 12.28 18 2167.39 1006.42 70 18 OFF-LA-10004345 Office Supplies Labels Avery 493 Texas 3.928 4 55.97 23.43 13 4 TEC-PH-10001552 Technology Phones I Need's 3d Hello Kitty Hybrid Silicone Case Cover for HTC One X 4g with 3d Hello Kitty Stylus Pen Green/pink Ohio 7.176 10 543.01 95.41 52 10 FUR-FU-10001979 Furniture Furnishings Dana Halogen Swing-Arm Architect Lamp Colorado 32.776 6 1114.39 288.42 28 6 FUR-FU-10001756 Furniture Furnishings Eldon Expressions Desk Accessory, Wood Photo Frame, Mahogany Texas 7.616 6 262.76 -7.62 20 6 TEC-CO-10003236 Technology Copiers Canon Image Class D660 Copier Montana 599.99 2 3959.93 1691.97 7 2 FUR-BO-10001972 Furniture Bookcases O'Sullivan 4-Shelf Bookcase in Odessa Pine Ohio 60.4 7 2739.75 -974.5 37 7 TEC-AC-10002800 Technology Accessories Plantronics Audio 478 Stereo USB Headset Pennsylvania 39.992 9 1619.68 514.9 34 9 FUR-FU-10003194 Furniture Furnishings Eldon Expressions Desk Accessory, Wood Pencil Holder, Oak Florida 7.5 4 107.2 6.76 15 4 FUR-FU-10000260 Furniture Furnishings 6" Cubicle Wall Clock, Black California 8.09 4 124.59 26.22 19 4 OFF-AP-10002191 Office Supplies Appliances Belkin 8 Outlet SurgeMaster II Gold Surge Protector Washington 59.98 5 737.75 89.97 15 5 FUR-CH-10003379 Furniture Chairs Global Commerce Series High-Back Swivel/Tilt Chairs New Jersey 284.6666667 9 7978.57 926.19 33 9 OFF-BI-10001071 Office Supplies Binders GBC ProClick Punch Binding System Minnesota 63.98 7 1573.91 562.12 31 7 OFF-SU-10004498 Office Supplies Supplies Martin-Yale Premier Letter Opener Washingt

5. Enriched Orders and Unit Testing

In [0]:
# Join orders with customer and product details
from pyspark.sql.functions import round
spark_orders_df = spark_orders_df.withColumn('Profit', round(spark_orders_df['Profit'], 2))

enriched_orders = spark_orders_df.join(
    enriched_customers.select('Customer_ID', 'Customer_Name', 'Country'), 
    on='Customer_ID', how='inner'
).join(
    enriched_products.select('Product_ID', 'Product_Name', 'Category', 'Sub-Category'), 
    on='Product_ID', how='inner'
)

display(enriched_orders)

# Unit tests for dataframes and functions

import pytest

def test_enriched_orders_columns():
    expected_columns = {
        'Row_ID', 'Order_ID', 'Order_Date', 'Ship_Date', 'Ship_Mode', 'Customer_ID',
        'Product_ID', 'Quantity', 'Price', 'Discount', 'Profit', 'Year',
        'Customer_Name', 'Country', 'Product_Name', 'Category', 'Sub-Category'
    }
    actual_columns = set(enriched_orders.columns)
    assert expected_columns.issubset(actual_columns), "enriched_orders missing expected columns."

def test_enriched_orders_no_nulls_in_keys():
    # Ensure no nulls in join keys
    null_customer = enriched_orders.filter(enriched_orders.Customer_ID.isNull()).count()
    null_product = enriched_orders.filter(enriched_orders.Product_ID.isNull()).count()
    assert null_customer == 0, "Null Customer_IDs found in enriched_orders."
    assert null_product == 0, "Null Product_IDs found in enriched_orders."

def test_profit_rounded():
    # Ensure Profit is rounded to 2 decimals
    from pyspark.sql.functions import length, split
    profits = enriched_orders.select('Profit').rdd.flatMap(lambda x: x).filter(lambda x: x is not None)
    for profit in profits.collect():
        assert round(profit, 2) == profit, "Profit is not rounded to 2 decimals."

def test_parse_date_valid():
    # Test parse_date function for valid and invalid input
    assert parse_date('01/01/2020') == pd.Timestamp('2020-01-01')
    assert pd.isna(parse_date('invalid-date'))

def test_orders_df_year_extraction():
    # Ensure Year column matches Order Date year
    for row in orders_df.itertuples():
        if pd.notna(row._asdict()['Order_Date']):
            assert row._asdict()['Year'] == row._asdict()['Order_Date'].year

def test_customers_df_no_phone_column():
    assert 'phone' not in customers_df.columns, "phone column not dropped from customers_df."

def test_products_df_column_renaming():
    assert "Product_ID" in products_df.columns, "Column renaming failed for Products DataFrame."

def test_orders_df_column_renaming():
    assert "Order_ID" in orders_df.columns, "Column renaming failed for Orders DataFrame."

Product_ID Customer_ID Row_ID Order_ID Order_Date Ship_Date Ship_Mode Quantity Price Discount Profit Year Customer_Name Country Product_Name Category Sub-Category FUR-CH-10002961 JK-15370 1 CA-2016-122581 2016-08-21T00:00:00.000Z 2016-08-25T00:00:00.000Z Standard Class 7 573.17 0.3 63.69 2016 Jay Kimmel United States Leather Task Chair, Black Furniture Chairs TEC-AC-10004659 BD-11320 2 CA-2017-117485 2017-09-23T00:00:00.000Z 2017-09-29T00:00:00.000Z Standard Class 4 291.96 0.0 102.19 2017 Bil Donatelli United States Imation Secure+ Hardware Encrypted USB 2.0 Flash Drive; 16GB Technology Accessories OFF-BI-10002824 LB-16795 3 US-2016-157490 2016-10-06T00:00:00.000Z 2016-10-07T00:00:00.000Z First Class 4 17.0 0.7 -14.92 2016 Laurel Beltran United States Recycled Easel Ring Binders Office Supplies Binders OFF-PA-10003349 KB-16315 4 CA-2015-111703 2015-07-02T00:00:00.000Z 2015-07-09T00:00:00.000Z Standard Class 3 15.55 0.2 5.64 2015 Karl Braun United States Xerox 1957 Office Supplies Paper TEC-AC-10003023 DO-13435 5 CA-2014-108903 2014-10-03T00:00:00.000Z 2014-10-03T00:00:00.000Z Same Day 3 142.49 0.2 -3.0 2014 Denny Ordway United States Logitech G105 Gaming Keyboard Technology Accessories OFF-BI-10004233 CB-12025 6 CA-2016-117583 2016-11-27T00:00:00.000Z 2016-11-30T00:00:00.000Z First Class 5 79.95 0.0 38.38 2016 Cassandra Brandow United States GBC Pre-Punched Binding Paper, Plastic, White, 8-1/2" x 11" Office Supplies Binders OFF-PA-10004470 SM-20005 7 CA-2014-148488 2014-12-10T00:00:00.000Z 2014-12-15T00:00:00.000Z Standard Class 2 11.0 0.0 5.23 2014 Sally Matthias United States Adams Write n' Stick Phone Message Book, 11" X 5 1/4", 200 Messages Office Supplies Paper FUR-FU-10001196 RD-19480 8 CA-2016-136434 2016-12-01T00:00:00.000Z 2016-12-07T00:00:00.000Z Standard Class 3 17.31 0.0 5.19 2016 Rick Duston United States DAX Cubicle Frames - 8x10 Furniture Furnishings OFF-ST-10000585 JM-16195 9 CA-2014-160094 2014-04-30T00:00:00.000Z 2014-05-02T00:00:00.000Z First Class 5 826.0 0.0 214.0 2014 Justin MacKendrick United States Economy Rollaway Files Office Supplies Storage OFF-ST-10003996 SC-20230 10 CA-2017-141747 2017-08-03T00:00:00.000Z 2017-08-08T00:00:00.000Z Second Class 1 16.06 0.0 4.18 2017 Scot Coram United States Letter/Legal File Tote with Clear Snap-On Lid, Black Granite Office Supplies Storage OFF-FA-10002280 BO-11350 11 CA-2017-132199 2017-05-03T00:00:00.000Z 2017-05-08T00:00:00.000Z Standard Class 2 8.0 0.2 2.8 2017 Bil Overfelt United States Advantus Plastic Paper Clips Office Supplies Fasteners OFF-BI-10001989 BD-11320 12 CA-2017-107125 2017-11-27T00:00:00.000Z 2017-12-02T00:00:00.000Z Standard Class 7 117.49 0.2 41.12 2017 Bil Donatelli United States Premium Transparent Presentation Covers by GBC Office Supplies Binders OFF-BI-10001460 AB-10105 13 CA-2017-153822 2017-09-19T00:00:00.000Z 2017-09-25T00:00:00.000Z Standard Class 4 18.18 0.7 -13.94 2017 Adrian Barton United States Plastic Binding Combs Office Supplies Binders TEC-AC-10002167 NP-18670 14 CA-2017-150091 2017-10-12T00:00:00.000Z 2017-10-16T00:00:00.000Z Standard Class 3 45.0 0.0 4.0 2017 Nra Paige United States Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive Technology Accessories FUR-FU-10001967 KD-16270 15 CA-2016-130407 2016-09-02T00:00:00.000Z 2016-09-06T00:00:00.000Z Standard Class 2 39.98 0.0 9.99 2016 Karen Danels United States Telescoping Adjustable Floor Lamp Furniture Furnishings FUR-FU-10003806 BF-11005 16 US-2016-105452 2016-07-28T00:00:00.000Z 2016-08-01T00:00:00.000Z Standard Class 5 302.0 0.6 -378.4 2016 Barry Franz United States Tenex Chairmat w/ Average Lip, 45" x 53" Furniture Furnishings OFF-BI-10004139 LE-16810 17 US-2014-117058 2014-05-27T00:00:00.000Z 2014-05-30T00:00:00.000Z First Class 6 17.46 0.8 -30.55 2014 Laurel Elliston United States Fellowes Presentation Covers for Comb Binding Machines Office Supplies Binders OFF-ST-10000991 TT-21070 18 CA-2017-122490 2017-11-13T00:00:00.000Z 2017-11-18T00:00:00.000Z Standard Class 3 344.

In [0]:
enriched_orders.write.mode("overwrite").saveAsTable("enriched_orders")

6. Calculate Profit and Unit Testing

In [0]:
from pyspark.sql import functions as F

# Annual profit analysis
profit_by_year = enriched_orders.groupby('Year').agg(
    F.sum('Profit').alias('Total_Profit')
)

# Product Category profit analysis
profit_by_category = enriched_orders.groupby('Category').agg(
    F.sum('Profit').alias('Total_Profit')
)

# Product Sub-Category profit analysis
profit_by_sub_category = enriched_orders.groupby('Sub-Category').agg(
    F.sum('Profit').alias('Total_Profit')
)

# Product Sub-Category profit analysis
profit_by_cust = enriched_orders.groupby('Customer_Name').agg(
    F.sum('Profit').alias('Total_Profit')
)

display(profit_by_year)
display(profit_by_category)
display(profit_by_sub_category)
display(profit_by_cust)

# Unit tests for the above dataframes and aggregations

import pytest

def test_profit_by_year_columns():
    expected_columns = {'Year', 'Total_Profit'}
    actual_columns = set(profit_by_year.columns)
    assert expected_columns == actual_columns, "profit_by_year columns mismatch."

def test_profit_by_category_columns():
    expected_columns = {'Category', 'Total_Profit'}
    actual_columns = set(profit_by_category.columns)
    assert expected_columns == actual_columns, "profit_by_category columns mismatch."

def test_profit_by_sub_category_columns():
    expected_columns = {'Sub-Category', 'Total_Profit'}
    actual_columns = set(profit_by_sub_category.columns)
    assert expected_columns == actual_columns, "profit_by_sub_category columns mismatch."

def test_profit_by_cust_columns():
    expected_columns = {'Customer_Name', 'Total_Profit'}
    actual_columns = set(profit_by_cust.columns)
    assert expected_columns == actual_columns, "profit_by_cust columns mismatch."

def test_total_profit_non_negative():
    # Total_Profit should not be negative in any aggregation (or can be zero/positive)
    for df in [profit_by_year, profit_by_category, profit_by_sub_category, profit_by_cust]:
        min_profit = df.agg(F.min('Total_Profit')).collect()[0][0]
        assert (min_profit is None) or (min_profit >= 0), "Total_Profit contains negative values."

def test_years_match_orders():
    # All years in profit_by_year should be present in enriched_orders
    years_orders = set(row['Year'] for row in enriched_orders.select('Year').distinct().collect())
    years_agg = set(row['Year'] for row in profit_by_year.select('Year').distinct().collect())
    assert years_agg.issubset(years_orders), "profit_by_year contains years not in enriched_orders."

def test_categories_match_orders():
    # All categories in profit_by_category should be present in enriched_orders
    cats_orders = set(row['Category'] for row in enriched_orders.select('Category').distinct().collect())
    cats_agg = set(row['Category'] for row in profit_by_category.select('Category').distinct().collect())
    assert cats_agg.issubset(cats_orders), "profit_by_category contains categories not in enriched_orders."

def test_sub_categories_match_orders():
    # All sub-categories in profit_by_sub_category should be present in enriched_orders
    subcats_orders = set(row['Sub-Category'] for row in enriched_orders.select('Sub-Category').distinct().collect())
    subcats_agg = set(row['Sub-Category'] for row in profit_by_sub_category.select('Sub-Category').distinct().collect())
    assert subcats_agg.issubset(subcats_orders), "profit_by_sub_category contains sub-categories not in enriched_orders."

def test_customers_match_orders():
    # All customer names in profit_by_cust should be present in enriched_orders
    cust_orders = set(row['Customer_Name'] for row in enriched_orders.select('Customer_Name').distinct().collect())
    cust_agg = set(row['Customer_Name'] for row in profit_by_cust.select('Customer_Name').distinct().collect())
    assert cust_agg.issubset(cust_orders), "profit_by_cust contains customer names not in enriched_orders."

Year Total_Profit 2016 67872.71 2015 63588.14999999997 2017 126920.96000000008 2014 40490.76

Category Total_Profit Office Supplies 128363.46999999997 Furniture 8583.789999999997 Technology 161925.32

Sub-Category Total_Profit Art 6379.9 Accessories 49076.42999999999 Binders 29671.890000000007 Fasteners 738.46 Bookcases -3287.659999999999 Envelopes 6201.64 Supplies -1224.87 Appliances 24009.730000000007 Machines -13501.519999999999 Paper 35538.630000000005 Furnishings 3649.74 Labels 5502.870000000001 Storage 21545.21999999999 Copiers 55617.89000000001 Chairs 25675.379999999997 Phones 70732.52 Tables -17453.67

Customer_Name Total_Profit Craig Yedwab 60.640000000000015 Odella Nelson -5.529999999999996 Keith Dawkins 3030.05 Philip Brown 263.27 Sean Braxton -2082.76 Vivek Grady -52.33 Craig Carroll 800.0600000000001 James Galang 1972.33 Art Foster -163.13 Daniel Lacy 4.389999999999933 Rachel Payne 59.52 Hallie Redmond 185.4 Steve Carroll 360.96999999999997 Anna Hberlin 1239.84 Patrick OBrill 23.89999999999995 Don Weiss 69.66000000000001 Emily Grady 103.9 Roger Demir 207.72 Bradley Drucker 1097.88 Harold Ryan 1197.3700000000001 Sonia Cooley 100.23 Astrea Jones 60.42 Shahi Hopkins -142.27999999999997 Sean Miller -1978.12 Nat Gilpin 313.63 Joni Waerman 32.509999999999984 Parhena Norris 192.04000000000002 Matt Connell 194.07999999999998 Darren Powers 241.69000000000003 Dan Lawera 325.89 Duane Huffman 116.67999999999999 Kristen Hastings 1227.13 Jennifer Halladay -25.86 Michael Granlund 171.44 Andy Gerbode -152.75 Doug OConnell 293.84000000000003 Alice McCarthy 287.49 Nancy Lomonaco 343.8 Clay Cheatham 34.3 Skye Norling -536.07 Hunter Lopez 5611.459999999999 Adrian Hane 56.93999999999997 Neil Ducich 443.3399999999999 Max Jones 1054.5399999999997 Monica Federle 456.86 Claire Gute 169.93 Aaron Bergman 129.68 Karen Carlisle 846.1400000000001 Claudia Bergmann 1161.77 Sibella Parks -118.38000000000002 Jack Lebron -207.31999999999996 Jane Waco 2174.0399999999995 Nra Paige 513.15 Kean Thornton 228.45999999999998 Bradley Nguyen 340.71999999999997 David Wiener -86.96999999999998 Brian Dahlen 548.73 Valerie Takahito -224.92999999999998 Dennis Kane 373.43 Brian Moss 2979.4400000000005 Karen Danels 1095.4599999999998 Randy Ferguson 633.67 Alex Russell -221.06 Michael Moore 81.44999999999999 Brian Stugart 238.72999999999996 Dorothy Wardle -244.50999999999996 Sanjit Chand 5839.14 Chuck Clark 611.0200000000001 Andrew Allen 445.9699999999999 Carol Darley -526.95 Cindy Chapman 154.85000000000002 Henry MacAllister 118.50999999999999 Art Ferguson 317.61999999999995 Doug Bickford 432.71 Vivek Sundaresam -317.08000000000004 Charlotte Melton 99.0 Dionis Lloyd -52.389999999999986 Troy Blackwell -136.47 Shaun Chance 379.57 Scott Cohen 670.98 Rob Dowd 801.2700000000001 Arthur Prichep 579.68 Dave Brooks 445.62999999999994 Ann Steele 131.75 Liz Preis 338.46000000000004 Pierre Wener 1253.76 Arianne Irving 851.0699999999999 Jim Radford -785.16 Kimberly Carter 157.23000000000002 Magdelene Morse 178.41000000000003 Chuck Magee 56.08 Todd Boyes 268.95 Roland Fjeld 711.83 Tom Ashbrook 4703.719999999999 Pauline Johnson 682.6800000000001 Lena Hernandez 536.3 Peter Fuller -639.02 Mark Van Huff 189.00999999999996 Brooke Gillingham 107.59 Darren Budd 233.41 Sung Pak 584.4200000000001 Edward Hooks 1358.23 Paul Prost 1533.89 Bil Overfelt 278.43 Jamie Kunitz 1225.5600000000002 Roland Murray 28.68 Joni Sundaresam -327.93 Randy Bradley -164.41000000000003 Pamela Coakley 272.68 Robert Dilbeck 835.77 Patrick Jones 442.14 Fred Chung 714.29 Eugene Hildebrand 312.19 Christopher Schild -475.39000000000004 Dean perceR 337.8099999999999 Erin Smith 220.28 Rick Wi lson 1574.55 Tamara Willingham 737.3899999999999 Dianna Wilson 1348.7499999999998 Gary McGarr 353.86 Dave Hallsten 1247.7399999999998 Dave Kipp 536.39 Paul Stevenson 260.29 Pauline Webber 1103.3 Thomas Thornton 283.22 Mick Crebagga -65.50999999999999 Ad am Hart 280.8 Theresa Swint 266.84999999999997 Guy Armstrong 170.85 Ritsa Hightower 0.3099999999999987 Toby Gnade 682.1700000000001 Jesus Ocampo 167.13 Dario Medina 107.5 Duane Noonan 540.5300000000001 Cynthia Voltz 98.70000000000002 Sue Ann Reed 596.78 Corey Catlett 331.27 Richard Bierner 475.03 Shahi Collister -3188.9999999999995 Berenike Kampe 51.30000000000001 William Brown 714.52 Jonathan Doherty 1099.6599999999996 Barry Franzsisch 309.62 Natalie Webber 1007.8599999999999 Thomas Seio 853.5899999999999 Robert Waldorf 707.5500000000001 Sung Shariari -65.35 Jason Fortune 91.63999999999999 Mark Hamilton 507.1700000000001 Brosina Hoffman 791.3600000000001 Helen Abelman 270.85 Frank Haw

In [0]:
%sql
-- Profit by year
SELECT Year, SUM(Profit) AS Total_Profit
FROM enriched_orders
GROUP BY Year;


Year Total_Profit 2016 67872.71 2015 63588.14999999997 2017 126920.96000000005 2014 40490.759999999995

In [0]:
%sql

-- Profit by year and product category
SELECT Year, Category, SUM(Profit) AS Total_Profit
FROM enriched_orders
GROUP BY Year, Category;


Year Category Total_Profit 2015 Office Supplies 24724.23 2016 Furniture 7877.399999999998 2017 Furniture 3426.2299999999996 2014 Technology 23359.75 2014 Furniture -5363.76 2014 Office Supplies 22494.770000000004 2016 Technology 24087.000000000004 2016 Office Supplies 35908.310000000005 2017 Technology 78258.56999999999 2015 Furniture 2643.9200000000005 2015 Technology 36220.0 2017 Office Supplies 45236.159999999996

In [0]:
%sql

-- Profit by customer
SELECT Customer_Name, SUM(Profit) AS Total_Profit
FROM enriched_orders
GROUP BY Customer_Name;


Customer_Name Total_Profit Craig Yedwab 60.64000000000002 Odella Nelson -5.529999999999987 Keith Dawkins 3030.05 Philip Brown 263.27 Sean Braxton -2082.76 Vivek Grady -52.33 Craig Carroll 800.0600000000001 James Galang 1972.3300000000002 Art Foster -163.13 Daniel Lacy 4.389999999999933 Rachel Payne 59.52 Hallie Redmond 185.4 Steve Carroll 360.96999999999997 Anna Hberlin 1239.84 Patrick OBrill 23.900000000000027 Don Weiss 69.66000000000001 Emily Grady 103.89999999999999 Roger Demir 207.72 Bradley Drucker 1097.88 Harold Ryan 1197.3700000000001 Sonia Cooley 100.23 Astrea Jones 60.42 Shahi Hopkins -142.27999999999997 Sean Miller -1978.1200000000001 Nat Gilpin 313.63 Joni Waerman 32.51 Parhena Norris 192.04000000000002 Matt Connell 194.08 Darren Powers 241.69 Dan Lawera 325.89 Duane Huffman 116.67999999999999 Kristen Hastings 1227.1299999999999 Jennifer Halladay -25.86 Michael Granlund 171.44000000000003 Andy Gerbode -152.75 Doug OConnell 293.84000000000003 Alice McCarthy 287.49 Nancy Lomonaco 343.8 Clay Cheatham 34.3 Skye Norling -536.07 Hunter Lopez 5611.459999999999 Adrian Hane 56.940000000000026 Neil Ducich 443.34 Max Jones 1054.54 Monica Federle 456.85999999999996 Claire Gute 169.93 Aaron Bergman 129.68 Karen Carlisle 846.1400000000001 Claudia Bergmann 1161.77 Sibella Parks -118.38000000000002 Jack Lebron -207.31999999999996 Jane Waco 2174.04 Nra Paige 513.1500000000001 Kean Thornton 228.46 Bradley Nguyen 340.71999999999997 David Wiener -86.97000000000003 Brian Dahlen 548.73 Valerie Takahito -224.93 Dennis Kane 373.43 Brian Moss 2979.4400000000005 Karen Danels 1095.4599999999998 Randy Ferguson 633.67 Alex Russell -221.06 Michael Moore 81.44999999999999 Brian Stugart 238.72999999999996 Dorothy Wardle -244.51 Sanjit Chand 5839.14 Chuck Clark 611.0200000000001 Andrew Allen 445.97 Carol Darley -526.95 Cindy Chapman 154.85 Henry MacAllister 118.51 Art Ferguson 317.62 Doug Bickford 432.71000000000004 Vivek Sundaresam -317.08000000000004 Charlotte Melton 99.0 Dionis Lloyd -52.39 Troy Blackwell -136.47 Shaun Chance 379.57 Scott Cohen 670.98 Rob Dowd 801.27 Arthur Prichep 579.68 Dave Brooks 445.63 Ann Steele 131.75 Liz Preis 338.46 Pierre Wener 1253.76 Arianne Irving 851.0700000000002 Jim Radford -785.16 Kimberly Carter 157.23000000000002 Magdelene Morse 178.41 Chuck Magee 56.08 Todd Boyes 268.95000000000005 Roland Fjeld 711.83 Tom Ashbrook 4703.719999999999 Pauline Johnson 682.6800000000001 Lena Hernandez 536.3 Peter Fuller -639.02 Mark Van Huff 189.01 Brooke Gillingham 107.59000000000002 Darren Budd 233.41 Sung Pak 584.4200000000001 Edward Hooks 1358.23 Paul Prost 1533.89 Bil Overfelt 278.43000000000006 Jamie Kunitz 1225.5600000000002 Roland Murray 28.68 Joni Sundaresam -327.93 Randy Bradley -164.41000000000003 Pamela Coakley 272.68 Robert Dilbeck 835.77 Patrick Jones 442.14 Fred Chung 714.29 Eugene Hildebrand 312.19 Christopher Schild -475.39 Dean perceR 337.8099999999999 Erin Smith 220.27999999999997 Rick Wi lson 1574.55 Tamara Willingham 737.3899999999999 Dianna Wilson 1348.7499999999998 Gary McGarr 353.86 Dave Hallsten 1247.7399999999998 Dave Kipp 536.39 Paul Stevenson 260.29 Pauline Webber 1103.3 Thomas Thornton 283.22 Mick Crebagga -65.50999999999999 Ad am Hart 280.8 Theresa Swint 266.8499999999999 Guy Armstrong 170.85 Ritsa Hightower 0.3099999999999987 Toby Gnade 682.1700000000001 Jesus Ocampo 167.13 Dario Medina 107.5 Duane Noonan 540.5299999999999 Cynthia Voltz 98.70000000000002 Sue Ann Reed 596.7800000000001 Corey Catlett 331.27000000000004 Richard Bierner 475.03 Shahi Collister -3188.9999999999995 Berenike Kampe 51.30000000000001 William Brown 714.52 Jonathan Doherty 1099.6599999999996 Barry Franzsisch 309.62 Natalie Webber 1007.8599999999999 Thomas Seio 853.59 Robert Waldorf 707.55 Sung Shariari -65.35 Jason Fortune 91.63999999999999 Mark Hamilton 507.1700000000001 Brosina Hoffman 791.3599999999999 Helen Abelman 270.85 Frank Hawley 25850.07 Susan Gilcrest -10.330000000000002 Tracy Collins 217.95000000000002 Stefania Perri

In [0]:
%sql

-- Profit by customer and year
SELECT Customer_Name, Year, SUM(Profit) AS Total_Profit
FROM enriched_orders
GROUP BY Customer_Name, Year;

Customer_Name Year Total_Profit Anna Chung 2014 -4.970000000000001 Marc Harrigan 2014 12.21 Arthur Wiediger 2017 164.78 Jonathan Doherty 2015 113.75999999999999 Chloris Kastensmidt 2017 223.07999999999998 Stewart Carmichael 2015 147.72 Clay Cheatham 2017 34.3 Ken Black 2015 66.42 Stuart Calhoun 2017 2.58 Magdelene Morse 2016 166.51 Lindsay Shagiari 2014 138.15999999999997 Thea Hendricks 2017 10.05 Katharine Harms 2014 261.33 Jennifer Braxton 2016 -98.62 Neoma Murray 2015 -30.669999999999995 Allen Armold 2016 122.72999999999999 Ed Braxton 2014 -127.42 Sue Ann Reed 2017 164.49 Benjamin Patterson 2017 20.58 Rick Bensley 2014 336.96 Sarah Jordon 2017 -26.880000000000003 Victoria Pisteka 2014 118.07 Ad am Hart 2017 -54.58 Jennifer Patt 2015 100.93 Stewart Carmichael 2016 -1337.23 Aaron Hawkins 2014 66.84 Paul Prost 2015 67.55999999999999 Luke Weiss 2016 428.45000000000005 Karl Braun 2017 69.64 Karen Carlisle 2016 523.0899999999999 Dianna Arnett 2017 35.07 Toby Gnade 2016 844.6400000000001 Jennifer Braxton 2017 251.19000000000003 Anne Pryor 2017 -11.07 Tracy P oddar 2016 104.74000000000002 Ken Lonsdale 2014 376.35999999999996 Anthony Jacobs 2014 -56.950000000000045 Sean Braxton 2014 -1272.36 Gary Hwang 2017 43.6 Noel Staavos 2016 -254.13 Paul MacIntyre 2015 -21.71 Raymond Messe 2017 202.52 Bil Donatelli 2017 201.69 Pierre Wener 2014 -86.27 Noah Childs 2016 -461.2 Patrick ODonnell 2014 132.18 Trudy Glocke 2014 89.42 Christine Sundaresam 2014 77.03 Luke Weiss 2017 67.07 Luke Schmidt 2014 167.72 Dean Braden 2016 -83.55999999999999 Lindsay Shagiari 2017 236.89000000000001 Tracy Blumstein 2015 -1556.32 Duane Noonan 2014 179.71999999999997 Chris Selesnick 2015 95.26 Fred Harton 2017 361.88 Khloe Miller 2014 3.0 Chad McGuire 2017 400.46999999999997 Bil Eplett 2016 47.24 Joni Waerman 2015 -201.65 Sanjit Engle 2016 2673.77 Erin Smith 2016 -99.22 Lena Creighton 2016 151.34 Brian Thompson 2016 176.51 Carol Darley 2017 -534.7 Julia Dunbar 2017 131.89000000000001 Rachel Payne 2015 -50.04 Thea Hudgings 2016 -76.64 Max Engle 2017 23.16000000000001 Tamara Willingham 2015 610.2999999999998 Julia West 2015 133.51 Art Ferguson 2016 390.78999999999996 Valerie Takahito 2015 -257.93 Mick Hernandez 2017 498.79 Nat Carroll 2015 323.65 Tom Ashbrook 2017 4599.2 Karl Braun 2014 -29.74 Kalyca Meade 2017 128.93 Tom Prescott 2016 -91.11000000000001 Maxwell Schwartz 2015 197.79000000000002 Anthony Jacobs 2017 208.05 Thomas Seio 2014 471.81 Brian Moss 2017 2633.99 Anne McFarland 2017 392.01 Mathew Reese 2017 129.07 Alice McCarthy 2016 9.97 Carol Triggs 2017 159.26 Steven Ward 2014 19.72 Liz Carlisle 2014 -128.09 Paul Stevenson 2016 3.44 Chuck Magee 2016 45.3 Patrick ODonnell 2016 128.98000000000002 Patrick Gardner 2015 -564.68 Katherine Nockton 2014 29.95 Joy Bell 2016 15.969999999999999 Christina Anderson 2015 118.66 Arthur Prichep 2014 420.69 Ellis Ballard 2017 81.7 Marina Lichtenstein 2014 486.5800000000001 Lindsay Williams 2017 340.51 Dorothy Wardle 2015 -371.25 Shui Tom 2015 27.01 Meg Tillman 2016 432.24999999999994 Nona Balk 2015 127.06 Rick Wi lson 2017 1649.1699999999996 Arianne Irving 2017 68.18 Theresa Swint 2016 -48.91 Dianna Wilson 2014 1154.67 Lena Radford 2016 240.49 Gary Mitchum 2016 102.51999999999998 Brian Stugart 2015 175.39000000000001 Barry Gonzalez 2015 -998.9100000000001 James Galang 2015 1293.73 Andrew Gjertsen 2017 25.049999999999997 Lori Olson 2015 34.45 Bradley Nguyen 2014 185.37 Barry Franzsisch 2017 12.779999999999994 Steven Ward 2016 48.510000000000005 Kat rina Edelman 2014 156.05 Lena Hernandez 2015 121.10999999999999 Brian Stugart 2016 62.25999999999999 Cindy Chapman 2017 40.35000000000001 Adrian Barton 2017 379.42 Eugene Moren 2016 968.57 Doug Bickford 2017 60.5 Sarah Jordon 2015 5.900000000000002 Arianne Irving 2016 485.32 Brian Moss 2014 81.65 Bart Watters 2016 126.59 Laura Armstrong 2016 1526.6499999999999 Don Weiss 2017 53.650000000000006 Mick Crebagga 2015 -74.41 Sean Miller 2017 34.28 Sample Company A 2016 118.86999999999999 K

In [0]:
pip install pytest pytest-ipynb

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
